# Simulating Basic Logic Gates

### EPS109 Fall 2022 Theresa Trang Tran

In [1]:
# imports
import numpy as np
import matplotlib.pyplot as plt

# imports for animations from lab7
%matplotlib osx
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

# from lab7
from matplotlib.animation import FFMpegWriter

## Gate Class

In [2]:
# A Gate object represents 1 logic gate (inverter/NAND/NOR)
class Gate:
    
    current_particles = [] # (x, y) coordinates of particles coming from an input of the gate
    wire0 = 0.7 # color of wire when its value is 0 
    wire1 = 0.3 # color of wire when its value is 1
    particle_color = 0.5
    
    # Constructor for Gate object
    # gate_type (string): "inverter", "nand", or "nor"
    # A (2D numpy array): matrix containing logic gates for animation
    # x, y (int): coordinates of upper left corner of gate in A
    def __init__(self, gate_type, A, x, y):
        if gate_type != "inverter" and gate_type != "nand" and gate_type != "nor":
            print("INVALID GATE TYPE")
        
        self.gate_type = gate_type
        arr = draw_gate(A, gate_type, x, y) # contains (x, y) coords of inputs/output of the gate
        
        # set coords of input/outputs
        self.input1coord = arr[0]
        if gate_type == "inverter": # inverter has 1 input gate, 1 output gate
            self.outputcoord = arr[1]
        else:
            self.input2coord = arr[1] # NAND/NOR have 2 input gates, 1 output gate
            self.outputcoord = arr[2]
            
        self.input1 = 0 # initialize input/output values to 0
        self.input2 = 0
        self.wiredin1gate = None # a different gate's output if this gate's top input is connected to one
        self.wiredin2gate = None # a different gate's output if this gate's bottom input is connected to one
        self.wiredoutgate = None # a different gate's input if this gate's output is connected to one
        self.threshold = 5 # number of particles for the gate to propagate particles; represents delay of gates
        self.coords = self.get_coords(gate_type, x, y) # all possible coordinates where a particle can be in the gate
        self.output = self.calc_output()
    
    # Returns a list containing all (x, y) coordinates where particles can be in a gate
    # gate_type (string): "inverter", "nand", or "nor"
    # x, y (int): coordinates of upper left corner of gate in A
    def get_coords(self, gate_type, x, y):
        coords = []
        if gate_type == "inverter":
            coords += [(x + i, y + 1) for i in range(1, 10)]
            coords += [(x + i, y + 2) for i in range(2, 9)]
            coords += [(x + i, y + 3) for i in range(3, 8)]
            coords += [(x + i, y + 4) for i in range(4, 7)]
            coords += [self.input1coord, self.outputcoord]
            coords += [(x + 5, y + 5)] # connects to inverter bubble
            coords += [(x + i, y + 6) for i in range(4, 7)] # space from inverter bubble
        elif gate_type == "nand":
            coords += [self.input1coord, self.input2coord, self.outputcoord]
            coords += [(x + i, y + 1) for i in range(1, 10)]
            coords += [(x + i, y + 2) for i in range(1, 10)]
            coords += [(x + i, y + 3) for i in range(2, 9)]
            coords += [(x + i, y + 4) for i in range(2, 9)]
            coords += [(x + i, y + 5) for i in range(2, 9)]
            coords += [(x + i, y + 6) for i in range(3, 8)]
            coords += [(x + i, y + 7) for i in range(4, 7)]
            coords += [(x + 5, y + 8)]
            coords += [(x + i, y + 9) for i in range(4, 7)] # space from inverter bubble
        elif gate_type == "nor":
            coords += [self.input1coord, self.input2coord, self.outputcoord]
            coords += [(x + 1, y + 2), (x + 9, y + 2)]
            coords += [(x + i, y + 3) for i in range(1, 4)]
            coords += [(x + i, y + 3) for i in range(7, 10)]
            coords += [(x + i, y + 4) for i in range(2, 9)]
            coords += [(x + i, y + 5) for i in range(2, 9)]
            coords += [(x + i, y + 6) for i in range(3, 8)]
            coords += [(x + i, y + 7) for i in range(3, 8)]
            coords += [(x + 5, y + 8), (x + 5, y + 9)]
            coords += [(x + i, y + 10) for i in range(4, 7)] # space from inverter bubble
        return coords
        
    # Sets the input of a gate to 0 or 1. Returns None
    # A (2D numpy array):  matrix containing logic gates for animation
    # input_num (int): 1 to add input to top input, 2 to add input to bottom input of gate
    # input_signal (int): 0 or 1
    def set_input(self, A, input_num, input_signal):
        # get color of wire
        wire_color = get_wire_color(input_signal)
            
        # get x, y values to reference where to draw input wire + set input fields
        if input_num == 1: # 1
            x = self.input1coord[0]
            y = self.input1coord[1]
            self.input1 = input_signal
        else: # input_num == 2
            x = self.input2coord[0]
            y = self.input2coord[1]
            self.input2 = input_signal
            
        # add input to A
        A[x - 1][y - 5:y] = wire_color # top of input wire
        A[x + 1][y - 5:y] = wire_color # bottom of input wire
        A[x][y - 5] = wire_color # left end of wire
          
        # change output whenever input changes
        #self.get_output()
        
        # add new particle coming from input node as long as input_signal == 1
        self.init_current_particle(A, x, y - 4, input_signal)
        
    def calc_output(self):
        # set output of current gate
        if self.gate_type == "inverter":
            return not self.input1
        elif self.gate_type == "nand":
            return not (self.input1 and self.input2)
        elif self.gate_type == "nor":
            return not (self.input1 or self.input2)
        
    # Changes the gate's output signal depending on the input signal. 
    # Changes the output wire color if the output changes. Returns None
    def get_output(self):
        # get output coords
        outX = self.outputcoord[0]
        outY = self.outputcoord[1]
        x_in_top = self.input1coord[0]
        y_in_top = self.input1coord[1]
        # open inputs so particles can go through
        if self.gate_type != "inverter":
            x_in_bottom = self.input2coord[0]
            y_in_bottom = self.input2coord[1]
            A[x_in_bottom][y_in_bottom] = 0
        A[x_in_top][y_in_top] = 0
        
        # set output of current gate
        self.output = self.calc_output()    
        
        # change inputs of other gates connected to the output of this current gate
        if self.count_particles() >= self.threshold and self.output == 1: # when threshold is reached + output is 1
            # set output of connected gates to 1 + change output wire color if it exists
            if self.wiredoutgate != None:
                if self.wiredoutgate.wiredin1gate == self:
                    self.wiredoutgate.input1 = self.output
                    input_num = 1
                elif self.wiredoutgate.wiredin2gate == self:
                    self.wiredoutgate.input2 = self.output
                    input_num = 2
                create_wire(A, self, self.wiredoutgate, input_num, wire_val=Gate.wire1)
            
            # open gate to allow particles to move through gate
            A[outX, outY] = 0  
        # have leftover particles from before output turned to 0
        elif self.count_particles() >= self.threshold and self.output == 0:
            # set output of connected gates to 0 + change output wire color if it exists
            if self.wiredoutgate != None:
                if self.wiredoutgate.wiredin1gate == self:
                    self.wiredoutgate.input1 = self.output
                    input_num = 1
                elif self.wiredoutgate.wiredin2gate == self:
                    self.wiredoutgate.input2 = self.output
                    input_num = 2
                create_wire(A, self, self.wiredoutgate, input_num, wire_val=Gate.wire0)
            
            # close gate to stop particles from moving
            A[outX, outY] = 1 
            
            # remove particles from gate
            for p_remove in self.coords:
                if p_remove in Gate.current_particles:
                    Gate.current_particles.remove(p_remove)
                    A[p_remove[0]][p_remove[1]] = 0
        # don't change anything when:
        # self.count_particles() < self.threshold and self.output == 1:
        # self.count_particles() < self.threshold and self.output == 0
        else:
            # close gate to stop particles from moving
            A[outX, outY] = 1
            
        # edge cases where all inputs are 0 and output is supposed to be 1
        inv_edge = self.gate_type == "inverter" and self.input1 == 0
        nand_edge = self.gate_type == "nand" and self.input1 == 0 and self.input2 == 0
        nor_edge = self.gate_type == "nor" and self.input1 == 0 and self.input2 == 0
        # add particles at inputs of gate
        if inv_edge or nand_edge or nor_edge:
            # add particle from top input
            x_in_top = self.input1coord[0]
            y_in_top = self.input1coord[1]
            if self.gate_type != "inverter":
                x_in_bottom = self.input2coord[0]
                y_in_bottom = self.input2coord[1]
                A[x_in_bottom][y_in_bottom] = 1
            self.init_current_particle(A, x_in_top, y_in_top + 1, 1)
            # close inputs so particles can't go backwards
            A[x_in_top][y_in_top] = 1
            
    # Creates a particle at (x, y) in A
    # A (2D numpy array):  matrix containing logic gates for animation
    # x, y (int): coordinates of where particle will be placed
    # input_signal (int): 0 or 1
    def init_current_particle(self, A, x, y, input_signal):
        # only move particles if output is 1
        if input_signal == 0:
            return
        # only add particle if one doesn't already occupy (x,y)
        if A[x, y] != 0.5:
            Gate.current_particles += [(x, y)]
            A[x, y] = Gate.particle_color
            
    # Returns the number of particles in the current gate
    def count_particles(self):
        num_particles = 0
        for particle in self.coords:
            x = particle[0]
            y = particle[1]
            if A[x][y] == Gate.particle_color:
                num_particles += 1
        return num_particles
    
# Resets the class variable current_particles
def clear_current_particles():
    Gate.current_particles = []
    
# Moves each particle that came from an input node
# A (2D numpy array):  matrix containing logic gates for animation
def random_current(A):
    n = A.shape[0]

    # move all particles
    i = 0
    while i < len(Gate.current_particles):
        x = Gate.current_particles[i][0]
        y = Gate.current_particles[i][1]
        lastX = x
        lastY = y
        r = np.random.random() # random float:  0.0 <= r < 1.0

        # if reach end of frame, particle leaves system
        if x <= 1 or x >= n - 2 or y <= 1 or y >= n - 2:
            Gate.current_particles.remove((x, y))
            continue

        up = A[x - 1][y]
        down = A[x + 1][y]
        right = A[x][y + 1]
        left = A[x][y - 1]

        # can't move where there is a wire, particle, or gate
        invalid_moves = [Gate.wire0, Gate.wire1, Gate.particle_color, 1]

        can_go_up = up not in invalid_moves
        can_go_down = down not in invalid_moves
        can_go_right = right not in invalid_moves
        can_go_left = left not in invalid_moves

        # more likely to go right if can go in any direction
        if can_go_up and can_go_down and can_go_right and can_go_left:
            if r < 0.2: # up 20%
                x -= 1
            elif r >= 0.2 and r < 0.4: # down 20%
                x += 1
            elif r >= 0.4 and r < 0.9: # right 50%
                y += 1
            elif r >= 0.9 and r < 1.0: # left 10%
                y -= 1
        # more likely to go right if can only go left/right
        elif can_go_right and can_go_left:
            if r < 0.1: # left 10%
                y -= 1
            elif r >= 0.1 and r < 1.0: # right 90%
                y += 1
        # equally likely to go in either direction if can only go in 2 directions
        elif can_go_up and can_go_down:
            if r < 0.5: # up 50%
                x -= 1
            elif r >= 0.5 and r < 1.0: # down 50%
                x += 1
        elif can_go_right and can_go_down:
            if r < 0.5: # right 50%
                y += 1
            elif r >= 0.5 and r < 1.0: # down 50%
                x += 1
        elif can_go_right and can_go_up:
            if r < 0.5: # right 50%
                y += 1
            elif r >= 0.5 and r < 1.0: # up 50%
                x -= 1
        elif can_go_up and can_go_left:
            if r < 0.5: # up 50%
                x -= 1
            elif r >= 0.5 and r < 1.0: # left 50%
                y -= 1
        elif can_go_down and can_go_left:
            if r < 0.5: # down 50%
                x += 1
            elif r >= 0.5 and r < 1.0: # left 50%
                y -= 1
        # if there's only one option for movement, move in that direction
        elif can_go_right:
            y += 1
        elif can_go_left:
            y -= 1
        elif can_go_up:
            x -= 1
        elif can_go_down:
            x += 1

        # change location of current particle and change animation
        Gate.current_particles[i] = (x, y)
        A[lastX][lastY] = 0
        A[x][y] = Gate.particle_color
        
        i += 1 # increment
        
# Returns a float of the color of the wire
# Returns a darker color if input is 1, lighter green if input is 0
# input_signal (int): 1 or 0
def get_wire_color(input_signal):
    if input_signal == 1:
        return Gate.wire1
    else:
        return Gate.wire0

## Drawing gate methods

In [3]:
# Draws a gate given its type, location, and the array to draw it on
# A (2D numpy array): matrix containing logic gates for animation
# gate_type (string): "inverter", "nand", or "nor"
# x, y (int): coordinates of upper left corner of gate in A
def draw_gate(A, gate_type, x, y):
    if gate_type == "inverter":
        return inverter(A, x, y)
    elif gate_type == "nand":
        return nand(A, x, y)
    elif gate_type == "nor":
        return nor(A, x, y)

# Create an inverter with upper left most coordinate at (x, y)
# Returns an array containing the coordinates of the input and output nodes
# A (2D numpy array): matrix containing logic gates for animation
# x, y (int): coordinates of upper left corner of gate in A
def inverter(A, x, y):
    # left side of inverter
    for i in range(x, x + 11):
        A[i][y] = 1
    # top of triangle, leaves for output gate
    for i in range(5):
        A[x + i][y + 1 + i] = 1
    # bottom of triangle, leaves for output gate
    for i in range(5):
        A[x + 10 - i][y + 1 + i] = 1
    # input gate
    A[x + 5][y] = 0
    # inverter bubble
    A[x + 4][y + 5] = 1
    A[x + 3][y + 6] = 1
    A[x + 4][y + 7] = 1
    A[x + 6][y + 5] = 1
    A[x + 7][y + 6] = 1
    A[x + 6][y + 7] = 1
    return [(x + 5, y), (x + 5, y + 7)]

# Create a NAND gate with upper left most coordinate at (x, y)
# Returns an array containing the coordinates of the inputs and output nodes
# A (2D numpy array): matrix containing logic gates for animation
# x, y (int): coordinates of upper left corner of gate in A
def nand(A, x, y):
    # left side of NAND gate
    for i in range(x, x + 11):
        A[i][y] = 1
    # top curve of NAND gate
    A[x][y:y + 3] = 1
    A[x + 1][y + 3:y + 6] = 1
    A[x + 2][y + 6] = 1
    A[x + 3][y + 7] = 1
    A[x + 4][y + 8] = 1
    A[x + 10][y:y + 3] = 1
    A[x + 9][y + 3:y + 6] = 1
    A[x + 8][y + 6] = 1
    A[x + 7][y + 7] = 1
    A[x + 6][y + 8] = 1
    # input opening
    A[x + 3][y] = 0 # top input
    A[x + 7][y] = 0 # bottom input
    # inverter bubble
    A[x + 4][y + 8] = 1
    A[x + 3][y + 9] = 1
    A[x + 4][y + 10] = 1
    A[x + 6][y + 8] = 1
    A[x + 7][y + 9] = 1
    A[x + 6][y + 10] = 1
    # [top input, bottom input, output]
    return [(x + 3, y), (x + 7, y), (x + 5, y + 10)]

# Create a NOR gate with upper left most coordinate at (x, y)
# Returns an array containing the coordinates of the inputs and output nodes
# A (2D numpy array): matrix containing logic gates for animation
# x, y (int): coordinates of upper left corner of gate in A
def nor(A, x, y):
    # left side of nor gate
    A[x][y] = 1
    A[x + 1][y + 1] = 1
    A[x + 2][y + 2] = 1
    A[x + 3][y + 2] = 1
    A[x + 4][y + 3] = 1
    A[x + 5][y + 3] = 1
    A[x + 10][y] = 1
    A[x + 9][y + 1] = 1
    A[x + 8][y + 2] = 1
    A[x + 7][y + 2] = 1
    A[x + 6][y + 3] = 1
    # top right
    A[x][y + 1:y + 4] = 1
    A[x + 1][y + 4] = 1
    A[x + 1][y + 5] = 1
    A[x + 2][y + 6] = 1
    A[x + 2][y + 7] = 1
    A[x + 3][y + 8] = 1
    A[x + 4][y + 8] = 1
    # bottom right 
    A[x + 10][y + 1:y + 4] = 1
    A[x + 9][y + 4] = 1
    A[x + 9][y + 5] = 1
    A[x + 8][y + 6] = 1
    A[x + 8][y + 7] = 1
    A[x + 7][y + 8] = 1
    A[x + 6][y + 8] = 1
    # input openings
    A[x + 3][y + 2] = 0 # top input
    A[x + 7][y + 2] = 0 # bottom input
    A[x + 4][y + 2] = 1
    A[x + 6][y + 2] = 1
    # inverter bubble
    A[x + 4][y + 9] = 1
    A[x + 3][y + 10] = 1
    A[x + 4][y + 11] = 1
    A[x + 6][y + 9] = 1
    A[x + 7][y + 10] = 1
    A[x + 6][y + 11] = 1
    # [top input, bottom input, output]
    return [(x + 3, y + 2), (x + 7, y + 2), (x + 5, y + 11)]

## Wiring

In [4]:
# Connect an output of one gate to the input of another gate with a wire. Assumes that 
# gateA is located to the left of gateB. Can be used to change the wire value. Returns None
# A (2D numpy array): matrix containing logic gates for animation
# gateA (Gate object): this gate's output will be connected to one of gateB's input
# gateB (Gate object): the output of gateA will be connected to this gate's input
# input_num (int): for an inverter, this will always be 1. For NAND/NOR gates, this will
#                  be 1 when you want to drive the top input, and 2 if you want to drive the bottom input
# wire_val (float): the color of the wire, default is 0.7, meaning the voltage is 0
def create_wire(A, gateA, gateB, input_num, wire_val=Gate.wire0):
    # get coord vals of where to connect wire & set relevant fields + set wireoutgate/wiredingate fields
    # set output gate fields
    gateA_x = gateA.outputcoord[0] # connect from (gateA_x,gateA_y) to (gateB_x, gateB_y)
    gateA_y = gateA.outputcoord[1]
    gateA.wiredoutgate = gateB
    # set input gate fields
    if input_num == 1:
        gateB_x = gateB.input1coord[0]
        gateB_y = gateB.input1coord[1]
        gateB.wiredin1gate = gateA
    else:
        gateB_x = gateB.input2coord[0]
        gateB_y = gateB.input2coord[1]
        gateB.wiredin2gate = gateA
    
    # change output of gateB
    #gateB.get_output()
    
    # create connecting wire
    x_diff = gateA_x - gateB_x # height diff betw the 2 gates
    A[gateA_x + 1][gateA_y + 1:gateA_y + 4] = wire_val
    A[gateA_x - 1][gateA_y + 1:gateA_y + 4] = wire_val
    # connecting wire should go down
    if x_diff >= 0:
        # make wire go up
        for i in range(x_diff + 1):
            A[gateA_x - 1 - i][gateA_y + 4] = wire_val
        # bottom of wire
        A[gateA_x + 1][gateA_y + 4:gateA_y + 7] = wire_val
        # form lower wire corner
        for i in range(x_diff):
            A[gateA_x - i][gateA_y + 6] = wire_val
        # form upper wire corner
        A[gateA_x - 1 - x_diff][gateA_y + 4:gateB_y] = wire_val
        # form bottom wire to connect to input of gateB
        A[gateA_x - x_diff + 1][gateA_y + 6:gateB_y] = wire_val
    # connecting wire should go up
    else:
        # make wire go down
        for i in range(abs(x_diff)):
            A[gateA_x + 1 + i][gateA_y + 4] = wire_val
        # bottom of wire
        A[gateA_x - x_diff + 1][gateA_y + 4:gateB_y] = wire_val
        # form upper wire corner
        A[gateA_x - 1][gateA_y + 4:gateA_y + 7] = wire_val
        for i in range(abs(x_diff)):
            A[gateA_x + i][gateA_y + 6] = wire_val
        # connect upper wire corner to input gateA
        A[gateA_x - x_diff - 1][gateA_y + 7:gateB_y] = wire_val
        
# Create an output wire to the right end of the frame
# gate (Gate object): gate to connect wire to
# maxY (int): max y value to connect wire to right end of frame
def output_wire(gate, maxY):
    if gate.output == 1 and gate.count_particles() >= gate.threshold:
        out_coords = gate.outputcoord
        x_out = out_coords[0]
        y_out = out_coords[1]
        A[x_out - 1][y_out:maxY] = Gate.wire1
        A[x_out + 1][y_out:maxY] = Gate.wire1
    else:
        out_coords = gate.outputcoord
        x_out = out_coords[0]
        y_out = out_coords[1]
        A[x_out - 1][y_out:maxY] = Gate.wire0
        A[x_out + 1][y_out:maxY] = Gate.wire0

## Main animation: More complex circuit

### Demonstrate behavior of individual gates

In [5]:
n = 165
A = np.zeros((n, n))
maxY = 165

clear_current_particles()

x_inv1 = 10
y_inv1 = 75
inv1 = Gate("inverter", A, x_inv1, y_inv1)
inv1.set_input(A, 1, 1)

x_inv2 = 25
y_inv2 = 75
inv2 = Gate("inverter", A, x_inv2, y_inv2)
inv2.set_input(A, 1, 0)

x_nor1 = 40
y_nor1 = 75
nor1 = Gate("nor", A, x_nor1, y_nor1)
nor1.set_input(A, 1, 1)
nor1.set_input(A, 2, 1)

x_nor2 = 55
y_nor2 = 75
nor2 = Gate("nor", A, x_nor2, y_nor2)
nor2.set_input(A, 1, 0)
nor2.set_input(A, 2, 1)

x_nor3 = 70
y_nor3 = 75
nor3 = Gate("nor", A, x_nor3, y_nor3)
nor3.set_input(A, 1, 1)
nor3.set_input(A, 2, 0)

x_nor4 = 85
y_nor4 = 75
nor4 = Gate("nor", A, x_nor4, y_nor4)
nor4.set_input(A, 1, 0)
nor4.set_input(A, 2, 0)

x_nand1 = 100
y_nand1 = 75
nand1 = Gate("nand", A, x_nand1, y_nand1)
nand1.set_input(A, 1, 1)
nand1.set_input(A, 2, 1)

x_nand2 = 115
y_nand2 = 75
nand2 = Gate("nand", A, x_nand2, y_nand2)
nand2.set_input(A, 1, 0)
nand2.set_input(A, 2, 1)

x_nand3 = 130
y_nand3 = 75
nand3 = Gate("nand", A, x_nand3, y_nand3)
nand3.set_input(A, 1, 1)
nand3.set_input(A, 2, 0)

x_nand4 = 145
y_nand4 = 75
nand4 = Gate("nand", A, x_nand4, y_nand4)
nand4.set_input(A, 1, 0)
nand4.set_input(A, 2, 0)

gates = [inv1, inv2, nor1, nor2, nor3, nor4, nand1, nand2, nand3, nand4]
for gate in gates:
    output_wire(gate, maxY)

plt.imshow(A, interpolation='nearest')
plt.show()

In [6]:
metadata = dict(title='CMOS Logic Gates: Simple', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata, bitrate=200000)
fig = plt.figure(dpi=150)

with writer.saving(fig, "cmos_logic_gates_simple.mp4", dpi=150):
    iter = 100
    for i in range(iter):
        inv1.set_input(A, 1, 1)
        inv2.set_input(A, 1, 0)
        nor1.set_input(A, 1, 1)
        nor1.set_input(A, 2, 1)
        nor2.set_input(A, 1, 0)
        nor2.set_input(A, 2, 1)
        nor3.set_input(A, 1, 1)
        nor3.set_input(A, 2, 0)
        nor4.set_input(A, 1, 0)
        nor4.set_input(A, 2, 0)
        nand1.set_input(A, 1, 1)
        nand1.set_input(A, 2, 1)
        nand2.set_input(A, 1, 0)
        nand2.set_input(A, 2, 1)
        nand3.set_input(A, 1, 1)
        nand3.set_input(A, 2, 0)
        nand4.set_input(A, 1, 0)
        nand4.set_input(A, 2, 0)
        
        # move all particles
        random_current(A)
        
        for gate in gates:
            gate.get_output()
            output_wire(gate, maxY)
        
        plt.show()
        plt.imshow(A, interpolation='nearest')
        plt.draw()
        plt.pause(0.05) # choose the time argument between 0.01 and 0.5
        writer.grab_frame()
        
        if i % 10 == 0:
            print(str(i) + "...")

0...
10...
20...
30...
40...
50...
60...
70...
80...
90...


### Initialize a complex circuit

In [7]:
n = 100
A = np.zeros((n, n))

clear_current_particles()

# first column of gates + set their inputs
x_inv1 = 5
y_inv1 = 10
inv1 = Gate("inverter", A, x_inv1, y_inv1)
inv1.set_input(A, 1, 1)

x_nor1 = 20
y_nor1 = 10
nor1 = Gate("nor", A, x_nor1, y_nor1)
nor1.set_input(A, 1, 0)
nor1.set_input(A, 2, 0)

x_nand1 = 35
y_nand1 = 10
nand1 = Gate("nand", A, x_nand1, y_nand1)
nand1.set_input(A, 1, 1)
nand1.set_input(A, 2, 0)

x_inv2 = 50
y_inv2 = 10
inv2 = Gate("inverter", A, x_inv2, y_inv2)
inv2.set_input(A, 1, 0)

x_nor2 = 65
y_nor2 = 10
nor2 = Gate("nor", A, x_nor2, y_nor2)
nor2.set_input(A, 1, 1)
nor2.set_input(A, 2, 1)

x_nand2 = 80
y_nand2 = 10
nand2 = Gate("nand", A, x_nand2, y_nand2)
nand2.set_input(A, 1, 0)
nand2.set_input(A, 2, 0)

# second column of gates
x_inv3 = 20
y_inv3 = 30
inv3 = Gate("inverter", A, x_inv3, y_inv3)
create_wire(A, nor1, inv3, 1) # connect nor1 w/this inverter

x_inv4 = 35
y_inv4 = 30
inv4 = Gate("inverter", A, x_inv4, y_inv4) 
create_wire(A, nand1, inv4, 1) # connect nand2 w/this inverter

x_inv5 = 50
y_inv5 = 30
inv5 = Gate("inverter", A, x_inv5, y_inv5) 
create_wire(A, inv2, inv5, 1) # connect inv2 w/this inverter

x_nand3 = 72
y_nand3 = 30
nand3 = Gate("nand", A, x_nand3, y_nand3)
create_wire(A, nor2, nand3, 1)
create_wire(A, nand2, nand3, 2)

x_inv6 = 5
y_inv6 = 30
inv6 = Gate("inverter", A, x_inv6, y_inv6) 
create_wire(A, inv1, inv6, 1) # connect inv2 w/this inverter

# 3rd column
x_nand4 = 14
y_nand4 = 50
nand4 = Gate("nand", A, x_nand4, y_nand4)
create_wire(A, inv6, nand4, 1)
create_wire(A, inv3, nand4, 2)

x_nor3 = 42
y_nor3 = 50
nor3 = Gate("nor", A, x_nor3, y_nor3)
create_wire(A, inv4, nor3, 1)
create_wire(A, inv5, nor3, 2)

x_inv7 = 72
y_inv7 = 50
inv7 = Gate("inverter", A, x_inv7, y_inv7)
create_wire(A, nand3, inv7, 1)

# 4th column
x_nor4 = 30
y_nor4 = 69
nor4 = Gate("nor", A, x_nor4, y_nor4)
create_wire(A, nand4, nor4, 1)
create_wire(A, nor3, nor4, 2)

x_inv8 = 72
y_inv8 = 69
inv8 = Gate("inverter", A, x_inv8, y_inv8)
create_wire(A, inv7, inv8, 1)

# 5th column
x_nand5 = 51
y_nand5 = 87
nand5 = Gate("nand", A, x_nand5, y_nand5)
create_wire(A, nor4, nand5, 1)
create_wire(A, inv8, nand5, 2)

output_wire(nand5, n)

plt.imshow(A, interpolation='nearest')
plt.show()

gates = [inv1, nor1, nand1, inv2, nor2, nand2, inv3, inv4, inv5, nand3, inv6, nand4, nor3, nor4, nand5, inv7, inv8]
print(len(gates))

17


### Run random walks to represent current flowing through circuit

In [8]:
# from lab7
maxY = n
metadata = dict(title='CMOS Logic Gates', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata, bitrate=200000)
fig = plt.figure(dpi=100)

driven_gates = [inv1, nor1, nand1, inv2, nor2, nand2]

with writer.saving(fig, "cmos_logic_gates.mp4", dpi=100):
    iter = 200
    for i in range(iter):
        # only need to drive gates with inputs
        inv1.set_input(A, 1, 1)
        nor1.set_input(A, 1, 0)
        nor1.set_input(A, 2, 0)
        nand1.set_input(A, 1, 1)
        nand1.set_input(A, 2, 0)
        inv2.set_input(A, 1, 0)
        nor2.set_input(A, 1, 1)
        nor2.set_input(A, 2, 1)
        nand2.set_input(A, 1, 0)
        nand2.set_input(A, 2, 0)
        
        # move particles
        random_current(A)
        
        # update input/output
        for gate in gates:
            gate.get_output()
            
        # update rightmost output wire
        output_wire(nand5, n)
        
        plt.imshow(A, interpolation='nearest')
        plt.show()
        plt.draw()
        plt.pause(0.05) # choose the time argument between 0.01 and 0.5
        writer.grab_frame()
        
        if i % 10 == 0:
            print(str(i) + "...")

0...
10...
20...
30...
40...
50...
60...
70...
80...
90...
100...
110...
120...
130...
140...
150...
160...
170...
180...
190...
